In [11]:
import asyncio
import websockets
import json
import pandas as pd
import nest_asyncio
from datetime import datetime as dt
from datetime import date, timedelta
import time
import plotly.graph_objects as go
nest_asyncio.apply()

#Time-related functions
def datetime_to_timestamp(datetime): return int(dt.timestamp(datetime)*1000)
def timestamp_to_datetime(timestamp): return dt.fromtimestamp(timestamp/1000)
def date_to_timestamp(date): return datetime_to_timestamp(dt.combine(date, dt.min.time()))

#Gathering and manipulating the crypto option data from the Deribit API        
async def call_api(msg):
    async with websockets.connect('wss://www.deribit.com/ws/api/v2') as websocket:
        await websocket.send(msg)
        while websocket.open:
            response = await websocket.recv()
            json_par = json.loads(response)
            return(json_par)
                    
class MarketData:
    
    def __init__(self, currency, start_date = dt.today().date()-timedelta(days = 5), end_date = dt.today().date()):
        self.currency = currency
        self.start_date = start_date
        self.end_date = end_date

    def msg(self, kind = "option", count = 1000, include_old = True, sorting = "asc"):
        return {"jsonrpc" : "2.0",
                "id" : 1888,
                "method" : "public/get_last_trades_by_currency_and_time",
                "params" : {"currency": self.currency, 
                            "kind": kind,
                            "start_timestamp": self.updated_start_timestamp,
                            "end_timestamp": date_to_timestamp(self.end_date),
                            "count": count,
                            "include_old": include_old,
                            "sorting": sorting
                           }
                }

    def option_data(self):
        has_more = True 
        trades_list = []
        self.updated_start_timestamp = date_to_timestamp(self.start_date)
        while has_more == True:
            data = asyncio.get_event_loop().run_until_complete(call_api(json.dumps(MarketData.msg(self))))
            trades_list.extend(data["result"]["trades"])
            has_more = data["result"]["has_more"]
            self.updated_start_timestamp = int(data["result"]["trades"][-1]["timestamp"]+1)

        option_data = pd.DataFrame(trades_list)
        option_data = option_data[["timestamp", "price", "instrument_name", "index_price", "direction", "amount", 'iv']]
        option_data["kind"] = option_data["instrument_name"].apply(lambda x: str(x).split("-")[0])
        option_data["maturity_date"] = option_data["instrument_name"].apply(lambda x: str(x).split("-")[1])
        option_data["maturity_date"] = option_data["maturity_date"].apply(lambda x: dt.strptime(x, "%d%b%y"))
        option_data["strike_price"] = option_data["instrument_name"].apply(lambda x: int(str(x).split("-")[2]))
        option_data["moneyness"] = option_data["index_price"]/option_data["strike_price"]
        option_data["option_type"] = option_data["instrument_name"].apply(lambda x: str(x).split("-")[3])
        option_data["price"] = (option_data["price"]*option_data["index_price"]).apply(lambda x: round(x,2))
        option_data["date_time"] = option_data["timestamp"].apply(timestamp_to_datetime)
        option_data["time_to_maturity"] = option_data['maturity_date'] - option_data["date_time"]
        option_data["time_to_maturity"] = option_data["time_to_maturity"].apply(lambda x: max(round(x.total_seconds()/31536000,3),1e-04))
        option_data['option_type'] = option_data['option_type'].apply(lambda x: str(x).lower())
        option_data["iv"] = round(option_data["iv"]/100,3)
        option_data["time_to_maturity"] = option_data["time_to_maturity"]*365
        option_data.drop(['timestamp'], axis=1, inplace = True)
        return option_data[['instrument_name','date_time','price', 'index_price', 'direction', 'amount', 'kind', 'time_to_maturity','strike_price', 'moneyness' ,'option_type', 'iv', 'maturity_date']]

#Figures
def iv_smile(option_data, date):
    data = option_data[option_data["date_time"].apply(lambda x: x.date()) == date]
    data.reset_index(inplace = True, drop = True)
    fig = go.Figure()
    for maturity_date in sorted(set(data["maturity_date"])):
        _data = data[data["maturity_date"] == maturity_date]
        fig.add_trace(go.Scatter(
            x=_data["moneyness"],
            y=_data["iv"],
            text = data["instrument_name"],
            customdata = data["moneyness"],
            hovertemplate=
                "<b>%{text}</b><br><br>" +
                "Implied volatility: %{y:.3f}<br>" +
                "Time to maturity: %{x:.0f} days <br>" +
                "Moneyness: %{customdata:.3f}<br>" +
                "<extra></extra>",
            mode='markers',
            marker=dict(
                size=4,   
                opacity=0.8
            ),
        name = f"{maturity_date.date()}"))
    fig.update_layout(
        title = f"{data['kind'][0]} Volatility Smiles of {date}",
        title_x=0.5,
        legend_title_text='Maturity dates',
        xaxis_title = "Moneyness",
        yaxis_title = "Implied Volatility", 
        hoverlabel = dict(
            bgcolor="white",
            font_size=16,
            font_family="Rockwell"))
    return fig

def iv_surface(option_data):
    fig = go.Figure(
        data = [go.Scatter3d(
            x=option_data["moneyness"],
            y=option_data["time_to_maturity"],
            z=option_data["iv"],
            name = "instrument_name",
            text = option_data["instrument_name"],
            customdata = option_data["date_time"],
            hovertemplate=
                "<b>%{text}</b><br><br>" +
                "Implied volatility: %{z:.3f}<br>" +
                "Time to maturity: %{y:.0f} days <br>" +
                "Moneyness: %{x:.3f}<br>" +
                "Date: %{customdata}<br>"+
                "<extra></extra>",
            mode='markers',
            marker=dict(
                size=4,
                color=option_data["iv"],                
                colorscale='Viridis',   
                opacity=0.8
            ))])

    fig.update_layout(
        title = f"{option_data['kind'][0]} Volatility Surface from {min(option_data['date_time']).date()} to {max(option_data['date_time']).date()}",
        title_x=0.5,
        scene = dict(
            xaxis_title = "Moneyness",
            yaxis_title = "Time to maturity (days)",
            zaxis_title = "Implied Volatility"), 
        autosize=False,
        width=1000,
        height=1000,
        hoverlabel = dict(
            bgcolor="white",
            font_size=16,
            font_family="Rockwell")
    )

    return fig

In [13]:
MarketData("BTC").option_data()

instrument_name               date_time    price  index_price  \
0       BTC-6JAN23-16500-C 2022-12-25 14:47:11.833   621.83     16806.32   
1      BTC-26DEC22-16750-P 2022-12-25 14:47:28.918    33.61     16806.77   
2      BTC-26DEC22-16750-P 2022-12-25 14:49:54.840    25.21     16806.28   
3       BTC-6JAN23-16500-P 2022-12-25 14:52:01.576   327.72     16805.91   
4      BTC-26DEC22-16750-P 2022-12-25 14:52:29.864    33.61     16806.95   
...                    ...                     ...      ...          ...   
14096  BTC-30DEC22-16000-P 2022-12-29 23:56:28.812     8.31     16619.70   
14097  BTC-24FEB23-16000-P 2022-12-29 23:56:51.559  1163.42     16620.23   
14098  BTC-24FEB23-19000-C 2022-12-29 23:57:51.470   498.55     16618.40   
14099  BTC-13JAN23-16500-C 2022-12-29 23:59:06.572   581.60     16617.20   
14100  BTC-30DEC22-16000-P 2022-12-29 23:59:13.258     8.31     16616.09   

      direction  amount kind  time_to_maturity  strike_price  moneyness  \
0          sell     0.1  BTC           11.3150         16500   1.018565   
1           buy     0.1  BTC            0.3650         16750   1.003389   
2          sell     0.5  BTC            0.3650         16750   1.003360   
3           buy     0.1  BTC           11.3150         16500   1.018540   
4          sell     0.2  BTC            0.3650         16750   1.003400   
...         ...     ...  ...               ...           ...        ...   
14096      sell     0.1  BTC            0.0365         16000   1.038731   
14097      sell     0.1  BTC           55.8450         16000   1.038764   
14098      sell     0.1  BTC           55.8450         19000   0.874653   
14099      sell     0.1  BTC           13.8700         16500   1.007103   
14100       buy     3.4  BTC            0.0365         16000   1.038506   

      option_type     iv maturity_date  
0               c  0.387    2023-01-06  
1               p  0.185    2022-12-26  
2               p  0.155    2022-12-26  
3               p  0.384    2023-01-06  
4               p  0.186    2022-12-26  
...           ...    ...           ...  
14096           p  0.720    2022-12-30  
14097           p  0.556    2023-02-24  
14098           c  0.501    2023-02-24  
14099           c  0.404    2023-01-13  
14100           p  0.717    2022-12-30  

[14101 rows x 13 columns]

In [15]:
iv_smile(option_data = MarketData("ETH").option_data(), date = dt.today().date()- timedelta(days = 2))

In [16]:
iv_surface(option_data = MarketData("BTC").option_data())